In [1]:
WEB_SITE_NAME = 'Entekhab.ir'

In [2]:
WEB_SITE_matrix = '../../models/' + WEB_SITE_NAME + '/view_matrix/lil_matrix.npz'
WEB_SITE_CONTENT_CSV = '../../models/content/' + WEB_SITE_NAME + '.csv'
WEB_SITE_itemindexer = '../../models/' + WEB_SITE_NAME + '/view_matrix/item_indexer.indexer'
WEB_SITE_userindexer = '../../models/' + WEB_SITE_NAME + '/view_matrix/user_indexer.indexer'
SAVING1 = './alisResult/' + WEB_SITE_NAME + '/ALS/ali_item_indexer_factorized.indexer'
SAVING2 = './alisResult/' + WEB_SITE_NAME + '/ALS/ali_user_indexer_factorized.indexer'
SAVING3 = './alisResult/' + WEB_SITE_NAME + '/ALS/ali_items_vectors.npy'
SAVING4 = './alisResult/' + WEB_SITE_NAME + '/ALS/ali_users_vectors.npy'
RESULTS_PATH = RESULTS = '../results/annoy_opt/' + WEB_SITE_NAME + '/'

In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import colors
from matplotlib.ticker import PercentFormatter
from tqdm import tqdm

import timeit
import time
import math

# ./indexer
from indexer import AppendIndexer
import ALS

# Annoy
from annoy import AnnoyIndex

#SKLearn 
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics import average_precision_score
from sklearn.metrics import pairwise_distances
from sklearn.model_selection import train_test_split

# scipy
from scipy.spatial import distance
from scipy.sparse import lil_matrix

In [4]:
WEBSITE_content = pd.read_csv(WEB_SITE_CONTENT_CSV)
print(WEBSITE_content.shape)
WEBSITE_content.tail(50)

(95321, 17)


Unnamed: 0       id                           created  \
95271      150028  8469212  2020-12-01 14:34:47.267597+03:30   
95272      150029  8469213  2020-12-01 14:34:47.268812+03:30   
95273      150030  8469214   2020-12-01 14:34:47.27012+03:30   
95274      150031  8469215  2020-12-01 14:34:47.271341+03:30   
95275      150032  8469216  2020-12-01 14:34:47.272561+03:30   
95276      150033  8469217  2020-12-01 14:34:47.273853+03:30   
95277      150034  8469218  2020-12-01 14:34:47.275048+03:30   
95278      150035  8469219  2020-12-01 14:34:47.276303+03:30   
95279      150036  8469220  2020-12-01 14:34:47.277518+03:30   
95280      150037  8469221  2020-12-01 14:34:47.278808+03:30   
95281      150038  8469222  2020-12-01 14:34:47.280045+03:30   
95282      150039  8469223  2020-12-01 14:34:47.281282+03:30   
95283      150040  8469224  2020-12-01 14:34:47.282553+03:30   
95284      150041  8469225  2020-12-01 14:34:47.283752+03:30   
95285      150042  8469226  2020-12-01 14:34:47.285001+03:30   
95286      150043  8469227  2020-12-01 14:34:47.286293+03:30   
95287      150044  8469228  2020-12-01 14:34:47.287565+03:30   
95288      150045  8469229  2020-12-01 14:34:47.288879+03:30   
95289      150046  8469230  2020-12-01 14:34:47.290159+03:30   
95290      150047  8469231  2020-12-01 14:34:47.291447+03:30   
95291      150048  8469232  2020-12-01 14:34:47.292674+03:30   
95292      150049  8469233  2020-12-01 14:34:47.293937+03:30   
95293      150050  8473251  2020-12-01 14:40:08.891787+03:30   
95294      150051  8473252  2020-12-01 14:40:08.893971+03:30   
95295      150059  8473342  2020-12-01 14:50:08.615873+03:30   
95296      150060  8473343  2020-12-01 14:50:08.617206+03:30   
95297      150061  8473344  2020-12-01 14:50:08.618486+03:30   
95298      150062  8473345  2020-12-01 14:50:08.620123+03:30   
95299      150063  8473397  2020-12-01 14:55:05.893154+03:30   
95300      150068  8473562  2020-12-01 15:15:06.258992+03:30   
95301      150071  8473618  2020-12-01 15:20:08.190228+03:30   
95302      150072  8473619  2020-12-01 15:20:08.191557+03:30   
95303      150076  8473699  2020-12-01 15:30:08.539365+03:30   
95304      150077  8473700  2020-12-01 15:30:08.540704+03:30   
95305      150079  8473849  2020-12-01 15:45:05.688198+03:30   
95306      150080  8473748  2020-12-01 15:35:05.969979+03:30   
95307      150081  8473749  2020-12-01 15:35:05.971181+03:30   
95308      150082  8473750  2020-12-01 15:35:05.972283+03:30   
95309      150084  8473797  2020-12-01 15:40:07.599272+03:30   
95310      150085  8473798  2020-12-01 15:40:07.600358+03:30   
95311      150089  8473848   2020-12-01 15:45:05.68684+03:30   
95312      150092  8473896  2020-12-01 15:50:08.800987+03:30   
95313      150096  8474069   2020-12-01 16:10:07.50603+03:30   
95314      150108  8474398  2020-12-01 16:50:08.253946+03:30   
95315      150109  8474399  2020-12-01 16:50:08.255596+03:30   
95316      150111  8474429  2020-12-01 16:55:06.143053+03:30   
95317      150113  8474544  2020-12-01 17:10:05.763308+03:30   
95318      150114  8474578  2020-12-01 17:15:06.361353+03:30   
95319      150115  8474579  2020-12-01 17:15:06.362908+03:30   
95320      150116  8474580  2020-12-01 17:15:06.364233+03:30   

                                          content_vector  \
95271  {0.363917618989944,-1.50092494487762,0.0530760...   
95272  {1.99103939533234,-0.697211146354675,-1.267899...   
95273  {-0.183786064386368,0.101832039654255,1.849017...   
95274  {1.02364492416382,-0.804460346698761,0.7175541...   
95275  {-0.480967044830322,0.00932194013148546,0.3719...   
95276  {0.23091359436512,-0.087655745446682,-0.444495...   
95277  {0.900073766708374,-0.575016558170319,0.106873...   
95278  {0.696282565593719,-0.339175462722778,-0.42948...   
95279  {1.34535896778107,-0.45953494310379,0.46755588...   
95280  {1.78237879276276,-0.0981960669159889,-0.14938...   
95281  {1.25870192050934,-0.70824784040451,-1.0733395...   
95282  {1.391805291175

In [5]:
WEBSITE_content = WEBSITE_content[WEBSITE_content.included == 't']
WEBSITE_content.shape

(95318, 17)

In [6]:
class ViewMatrix:
    def __init__(self, path):
        self.path = path
        self.original = True
        self.item_indexer = AppendIndexer.load(WEB_SITE_itemindexer)
        self.user_indexer = AppendIndexer.load(WEB_SITE_userindexer)
        
    def load_matrix(path):
        
        matrix = ViewMatrix(path)
        try:
            matrix.view_matrix = ViewMatrix \
                .load_sparse_lil(path)
        except:
            print('Error: loading', path)

        return matrix

    def load_sparse_lil(filename):
        loader = np.load(filename, allow_pickle=True)
        result = lil_matrix(tuple(loader["shape"]), dtype=str(loader["dtype"]))
        result.data = loader["data"]
        result.rows = loader["rows"]
        return result
    
    def make_dense(self, user_min_view, item_min_view):
        self.original = False
        while True:
            removed_rows_cnt = self.trim_users_with_few_views(user_min_view)
            removed_columns_cnt = self.trim_columns_with_few_views(item_min_view)
            if not removed_columns_cnt and not removed_rows_cnt:
                break

    def trim_users_with_few_views(self, user_min_view):
        removing_row_indices = list(np.where(self.view_matrix.getnnz(1) < user_min_view)[0])
        print('Number of users which should be deleted:', len(removing_row_indices))
        self.trim_user_indices(to_remove_indices=removing_row_indices)
        return len(removing_row_indices)

    def trim_columns_with_few_views(self, column_min_view):
        removing_column_indices = list(np.where(self.view_matrix.getnnz(0) < column_min_view)[0])
        print('Number products which should be deleted:', len(removing_column_indices))
        self.trim_column_indices(to_remove_indices=removing_column_indices)
        return len(removing_column_indices)
    
    def trim_user_indices(self, to_remove_indices):
        self.user_indexer.remove_indexes(to_remove_indices)
        self.view_matrix = ViewMatrix.delete_row_lil(self.view_matrix, to_remove_indices)
    
    def trim_column_indices(self, to_remove_indices):
        self.item_indexer.remove_indexes(to_remove_indices)
        self.view_matrix = ViewMatrix.delete_column_lil(self.view_matrix, to_remove_indices)
    
    def delete_column_lil(mat: lil_matrix, *i) -> lil_matrix:
        mat = mat.transpose()
        mat = ViewMatrix.delete_row_lil(mat, *i)
        return mat.transpose()
    
    def delete_row_lil(mat: lil_matrix, *i) -> lil_matrix:
        if not isinstance(mat, lil_matrix):
            raise ValueError("works only for LIL format -- use .tolil() first")
        mat = mat.copy()
        mat.rows = np.delete(mat.rows, i)
        mat.data = np.delete(mat.data, i)
        mat._shape = (mat.rows.shape[0], mat._shape[1])
        return mat
    def to_csr(self):
        train_data = self.view_matrix.astype(np.float64)
        train_data = train_data.tocoo()
        train_data.data = np.log10(train_data.data) + 1
        train_data = train_data.tocsr()
        return train_data

In [7]:
def CFTrain(path: str, _alpha = 20, factors = 20):
    now = time.time()
    matrix = ViewMatrix.load_matrix(path)
    print('View matrix loaded in', time.time() - now, 'seconds.')

    now = time.time()
    sparce_matrix = matrix.to_csr()
    matrix.make_dense(user_min_view = 3, 
                      item_min_view = 3)
    print('matrix has been made dense in', time.time() - now, 'seconds.')

    als_model = ALS.Als(num_factors = 60,
                        iterations = 15,
                        num_threads = 15,
                        alpha = 100)

    implicit_matrix = matrix.to_csr()
    
    now = time.time()
    print(implicit_matrix.shape)
    als_model.fit(implicit_matrix)
    alsTime = time.time() - now
    print('ALS model is fitted in', time.time() - now, 'seconds.')
    
    print('Saving Data ...')
    matrix.item_indexer.dump(SAVING1)
    matrix.user_indexer.dump(SAVING2)
    np.save(SAVING3, als_model.item_vectors)
    np.save(SAVING4, als_model.user_vectors)
    
    return sparce_matrix, implicit_matrix, als_model.item_vectors, als_model.user_vectors, item_indexer, user_indexer, alsTime

In [8]:
sparce_matrix, implicit_matrix, item_vectors, user_vectors, item_indexer, user_indexer, alsTime = \
CFTrain(WEB_SITE_matrix, factors = 60)

View matrix loaded in 15.096948385238647 seconds.
Number of users which should be deleted: 3778465
Number products which should be deleted: 57155
Number of users which should be deleted: 3067
Number products which should be deleted: 193
Number of users which should be deleted: 137
Number products which should be deleted: 9
Number of users which should be deleted: 8
Number products which should be deleted: 1
Number of users which should be deleted: 1
Number products which should be deleted: 0
Number of users which should be deleted: 0
Number products which should be deleted: 0
matrix has been made dense in 54.92648386955261 seconds.
(412624, 8176)
ALS model is fitted in 468.9752368927002 seconds.
Saving Data ...


In [10]:
ids = WEBSITE_content['id'].tolist()

In [11]:
print(item_vectors.shape)

(8176, 60)


In [12]:
print('sparce matrix:\t', sparce_matrix.shape)
print('implicit matrix:', implicit_matrix.shape)
print('item vectors:\t', item_vectors.shape)
print('users vectors:\t', user_vectors.shape)

sparce matrix:	 (4194302, 65534)
implicit matrix: (412624, 8176)
item vectors:	 (8176, 60)
users vectors:	 (412624, 60)


In [13]:
print('user tokens:\t', np.array(list(user_indexer.get_items())).shape)
print('item ids:\t', np.array(list(item_indexer.get_items())).shape)

user tokens:	 (412624,)
item ids:	 (8176,)


## Vectorized

In [14]:
ratings = user_vectors.dot(item_vectors.T)
print(ratings.shape)

(14974, 2069)


In [15]:
row, col = implicit_matrix.nonzero()
for i, j in zip(row, col):
    ratings[i, j] = 0
users_recoms2 = []
for user_ratings in tqdm(ratings):
    recoms = np.argsort(user_ratings)[-13:][::-1]
    user_recoms = []
    for r in recoms:
        rec = item_indexer.reverse_get(r)
        if int(rec) in ids:
#             user_recoms.append(r)
            user_recoms.append(rec)
    users_recoms2.append(user_recoms)

100%|██████████| 14974/14974 [00:08<00:00, 1852.62it/s]


In [16]:
users = list(user_indexer.get_items())
print(len(users_recoms2), len(list(user_indexer.get_items())))

14974 14974


## parallel

In [14]:
user_ranges = [i for i in range(0,len(user_vectors),700)]
user_ranges.append(len(user_vectors))
item_ranges = [i for i in range(0,len(item_vectors),1000)]
item_ranges.append(len(item_vectors))

In [15]:
print(item_ranges)

[0, 1000, 2000, 3000, 4000, 5000, 6000, 7000, 8000, 8176]


In [16]:
users_recoms = []
for i in tqdm(range(len(user_ranges)-1)):
    m = []
    for j in range(len(item_ranges)-1):
        temp = user_vectors[user_ranges[i]:user_ranges[i+1]].dot(item_vectors[item_ranges[j]:item_ranges[j+1]].T)
        if not len(m):
            m = temp
        else:
            m = np.concatenate((m, temp), 1)
    row, col = implicit_matrix[i:i+1,:].nonzero()
    for i, j in zip(row, col):
        m[i, j] = 0
    for user_ratings in m:
        recoms = np.argsort(user_ratings)[-13:][::-1]
        user_recoms = []
        for r in recoms:
            rec = item_indexer.reverse_get(r)
            if int(rec) in ids:
    #             user_recoms.append(r)
                user_recoms.append(rec)
        users_recoms.append(user_recoms)

100%|██████████| 590/590 [1:24:18<00:00,  8.57s/it]


In [17]:
users = list(user_indexer.get_items())
print(len(users_recoms), len(list(user_indexer.get_items())))

412624 412624


## check

In [23]:
def check(user_num = 100):
    row, col = implicit_matrix.nonzero()
    print('---user:', users[user_num], '---')
    print('what user saw:')
    for i in col[row == user_num]:
        print(WEBSITE_content[WEBSITE_content['id'] == int(item_indexer.reverse_get(i))].title.values)
    print('what we recommend:')
    for i in users_recoms[user_num]:
        print(WEBSITE_content[WEBSITE_content['id'] == int(i)].title.values)

In [24]:
for i in range(0,len(users_recoms), 14):
    check(i)

---user: 02fb517a-85ee-4e5e-ce00-50c8f3c384d2 ---
what user saw:
['معرفی 25 فیلم با پیچیده ترین پایان بندی ها در تاریخ سینما - پروشات']
['12 فیلم برتر تاریخ سینما با محوریت CIA (سازمان سیا) - پروشات']
['لیست بهترین فیلم هایی که با موضوع فرار از زندان ساخته شده اند - پروشات']
['معرفی 10 فیلم جذاب و دیدنی درباره تروریسم که شاید دوست داشته باشید تماشا کنید - پروشات']
what we recommend:
['لیست زننده\u200cترین و زجرآورترین فیلم\u200cهای تاریخ سینما که هرگز فراموش نخواهید کرد - پروشات']
['لیست 20 تایی خشن ترین فیلم های تاریخ سینما که نباید از دست بدهید - پروشات']
['11 انیمه برتر تاریخ با موضوع فرشتگان که باید ببینید - پروشات']
['12 فیلم جذاب و دیدنی شبیه فیلم "تک تیرانداز آمریکایی" (American Sniper) که باید تماشا کنید - پروشات']
['20 فیلم برتر ژانر آدم ربایی در تاریخ سینما که باید ببینید - پروشات']
['بهترین فیلم های دنزل واشینگتن که باید ببینید - پروشات']
['معرفی بهترین فیلم های تاریخ سینما با موضوع اعتیاد و مواد مخدر - پروشات']
['معرفی 26 فیلم جذاب و دیدنی درباره سرقت در تاریخ سینما که باید

['لیست بهترین فیلم های شاهرخ خان (Shahrukh Khan) که باید تماشا کنید - پروشات']
['لیست بهترین فیلم های هندی که باید تماشا کنید - پروشات']
['10 فیلم برتر "کیت بلانشت" (Cate Blanchett) بر اساس امتیاز راتن تومیتوز - پروشات']
['لیست بهترین فیلم های سلمان خان (Salman Khan) که باید تماشا کنید - پروشات']
['لیست بهترین فیلم های عامر خان (Aamir Khan) که باید تماشا کنید - پروشات']
['12 فیلم برتر هریتیک روشن (Hrithik Roshan) که باید تماشا کنید - پروشات']
['15 فیلم نینجایی جذاب و دیدنی در تاریخ سینما که باید تماشا کنید - پروشات']
['30 فیلم برتر رمانتیک تاریخ سینما - پروشات']
['معرفی تمام فیلم های تام کروز از بدترین تا بهترین، 42 اثر سینمایی پرخرج - پروشات']
['رده بندی برترین فیلم\u200cهای "اما استون" (Emma Stone) - پروشات']
['25 هنر رزمی مرگبار در جهان را بشناسید - پروشات']
---user: d0b702bb-f0d3-40a8-c0fd-c97a6652ec3c ---
what user saw:
['لیست 30 فیلم برتر آخرالزمانی در تاریخ سینما که باید ببینید - پروشات']
['8 فیلم برتر تاریخ درباره خدایان و اساطیر یونان به همراه تریلر - پروشات']
['رتبه\u200cبندی

['7 انیمه جذاب و دیدنی شبیه انیمه “جوجوتسو کایسن” (Jujutsu Kaisen) که باید تماشا کنید']
['بهترین انیمه های شبیه “شیطان کش” (Demon Slayer: Kimetsu no Yaiba)']
['معرفی بهترین انیمه های مشابه “موشوکو تنسی:تجسم بیکاری”']
what we recommend:
['7 انیمه جذاب و دیدنی شبیه انیمه "شوالیه و جادو" (Knight’s & Magic) که باید تماشا کنید - پروشات']
['معرفی بهترین انیمه های مشابه “موشوکو تنسی:تجسم بیکاری”']
['بهترین انیمه های شبیه “شیطان کش” (Demon Slayer: Kimetsu no Yaiba)']
['7 انیمه جذاب و دیدنی شبیه انیمه "غارتگر" (Plunderer) که باید تماشا کنید - پروشات']
['معرفی 12 انیمه برتر ژانر ایسکای در تاریخ انیمه سازی - پروشات']
['7 انیمه جذاب و دیدنی شبیه انیمه "بی نظم در دبیرستان جادو" (The Irregular at Magic High School) - پروشات']
['7 انیمه جذاب و دیدنی شبیه انیمه “جوجوتسو کایسن” (Jujutsu Kaisen) که باید تماشا کنید']
['4 انیمه جذاب و دیدنی شبیه "درخشنده" (Radiant) که باید تماشا کنید - پروشات']
['7 سریال جذاب و دیدنی شبیه سریال "افسانه کورا" (The Legend of Korra) که باید تماشا کنید - پروشات']
['10 انیمه ج

['لیست انیمه ۹ تا از بهترین انیمه\u200cهای چینی به انتخاب پروشات - پروشات']
---user: c176b989c2167fd707e9075da7e6082a ---
what user saw:
['25 شخصیت قدرتمند دنیای مارول از بین ابرقهرمانان و ابرشرورها - پروشات']
['لیست 25 تایی قوی\u200cترین اعضای تیم انتقام\u200cجویان در تاریخ کمیک\u200cهای مارول - پروشات']
['25 شخصیت قدرتمند دنیای مارول از بین ابرقهرمانان و ابرشرورها - صفحه 2 از 3 - پروشات']
what we recommend:
['25 شخصیت قدرتمند دنیای مارول از بین ابرقهرمانان و ابرشرورها - پروشات']
['لیست 25 تایی قوی\u200cترین اعضای تیم انتقام\u200cجویان در تاریخ کمیک\u200cهای مارول - پروشات']
['25 شخصیت قدرتمند دنیای مارول از بین ابرقهرمانان و ابرشرورها - صفحه 2 از 3 - پروشات']
['25 شخصیت قدرتمند دنیای مارول از بین ابرقهرمانان و ابرشرورها - صفحه 3 از 3 - پروشات']
['رده بندی تمام اعضای انتقامجویان، از قویترین تا ضعیف ترین - پروشات']
['25 ابر قهرمان قدرتمند تمام زمان\u200cها به همراه تصاویر - پروشات']
['10 شخصیت مارول که از دی سی الهام گرفته شده اند - پروشات']
['لیست قدرتمندترین موجودات کیهانی در دنیای م

['100 فیلم عاشقانه تاریخ سینما که تا ابد در قلب و خاطرمان جاودانه شده اند - صفحه 3 از 5 - پروشات']
['لیست بهترین فیلم های کره ای که در سال 2018 اکران شدند - پروشات']
['25 فیلم برتر کره\u200cای تاریخ سینما - پروشات']
['لیست بهترین فیلم های سلمان خان (Salman Khan) که باید تماشا کنید - پروشات']
['لیست بهترین فیلم های شاهرخ خان (Shahrukh Khan) که باید تماشا کنید - پروشات']
---user: 65e23b29-904c2-25ad4-4b862-2b54cd12b660b ---
what user saw:
['7 انیمه جذاب و دیدنی شبیه انیمه "غارتگر" (Plunderer) که باید تماشا کنید - پروشات']
['لیست 30 شخصیت برتر در تاریخ انیمه ها - پروشات']
['بهترین انیمه های مشابه “ناکجا آباد موعود” (The Promised Neverland)']
what we recommend:
['لیست 30 شخصیت برتر در تاریخ انیمه ها - پروشات']
['7 انیمه جذاب و دیدنی شبیه انیمه "غارتگر" (Plunderer) که باید تماشا کنید - پروشات']
['بهترین انیمه های مشابه “ناکجا آباد موعود” (The Promised Neverland)']
['معرفی 10 انیمه جذاب و دیدنی با ژانر حارم در سال 2019 که باید تماشا کنید - پروشات']
['7 انیمه جذاب و دیدنی شبیه انیمه “جوجوتسو 

...

['معرفی 10 فیلم جنجالی که در برخی کشورهای جهان مجوز پخش ندارند - پروشات']
['معرفی 16 فیلم جذاب و دیدنی شبیه "پیچ اشتباهی" (Wrong Turn) - پروشات']
['انیمه لیست 50 تایی از بهترین انیمه های سریالی تاریخ به انتخاب پروشات - پروشات']
['معرفی بهترین فیلم های رازآلود تاریخ سینما - پروشات']
['معرفی 10 فیلم جذاب و دیدنی شبیه "اتاق" (Room) - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه "الدبوی" (Oldboy) - پروشات']
['10 حقیقت جالب پنهان درباره ایلومیناتی - پروشات']
['لیست بهترین فیلم های جن گیری در تاریخ سینما - پروشات']
---user: b5ed23c7-78c68-8442e-e33c5-57e7541ad753f ---
what user saw:
['12 فیلم جذاب و دیدنی شبیه فیلم "دونده مارپیچ" (The Maze Runner) - پروشات']
['لیست 30 فیلم برتر آخرالزمانی در تاریخ سینما که باید ببینید - پروشات']
['12 فیلم برتر لهستانی در تاریخ فیلم سازی این کشور - پروشات']
what we recommend:
['لیست 30 فیلم برتر آخرالزمانی در تاریخ سینما که باید ببینید - پروشات']
['12 فیلم جذاب و دیدنی شبیه فیلم "دونده مارپیچ" (The Maze Runner) - پروشات']
['12 فیلم برتر لهستانی در تاریخ فیلم سا

['10 حقیقت درباره فیلم “داستان دو خواهر” (A Tale Of Two Sisters) محصول کره\u200cجنوبی']
---user: e51af950-033d3-3c6dd-dedd4-40218f0dd6f08 ---
what user saw:
['37 انیمیشن برتر تاریخ سینما که باید تماشا کنید - پروشات']
['رده بندی تمام اعضای انتقامجویان، از قویترین تا ضعیف ترین - پروشات']
['لیست بهترین انیمیشن\u200cهای سال 2020 که در انتظار اکرانشان هستیم - پروشات']
['مقایسه ابرقهرمان های سینما: مرد آهنی در برابر مرد عنکبوتی. کدام یک قویتر است؟ - پروشات']
what we recommend:
['رده بندی تمام اعضای انتقامجویان، از قویترین تا ضعیف ترین - پروشات']
['37 انیمیشن برتر تاریخ سینما که باید تماشا کنید - پروشات']
['لیست بهترین انیمیشن\u200cهای سال 2020 که در انتظار اکرانشان هستیم - پروشات']
['مقایسه ابرقهرمان های سینما: مرد آهنی در برابر مرد عنکبوتی. کدام یک قویتر است؟ - پروشات']
['لیست 25 تایی قوی\u200cترین اعضای تیم انتقام\u200cجویان در تاریخ کمیک\u200cهای مارول - پروشات']
['10 شخصیت مارول که از دی سی الهام گرفته شده اند - پروشات']
['25 ابر قهرمان قدرتمند تمام زمان\u200cها به همراه تصاویر - پروشات'

['بهترین انیمیشن های سال 2019-2020 که حتما باید تماشا کنید - پروشات']
['37 انیمیشن برتر تاریخ سینما که باید تماشا کنید - پروشات']
['25 انیمیشن کوتاه برتر کمپانی پیکسار - پروشات']
['لیست بهترین انیمیشن\u200cهای سال 2020 که در انتظار اکرانشان هستیم - پروشات']
what we recommend:
['بهترین انیمیشن های سال 2019-2020 که حتما باید تماشا کنید - پروشات']
['37 انیمیشن برتر تاریخ سینما که باید تماشا کنید - پروشات']
['لیست بهترین انیمیشن\u200cهای سال 2020 که در انتظار اکرانشان هستیم - پروشات']
['لیست بهترین انیمیشن هایی که در سال 2018 اکران شدند - پروشات']
['25 انیمیشن کوتاه برتر کمپانی پیکسار - پروشات']
['بهترین فیلم های کمپانی دیزنی که در سال 2019-2020 اکران خواهند شد - پروشات']
['رده بندی تمام فیلم های کمپانی دیزنی که در سال 2018 اکران شدند - پروشات']
['12 فیلم انیمیشن پیکسار که تأثیر روان\u200cشناسانه عمیق داشتند - پروشات']
['لیست بهترین انیمه های عاشقانه سینمایی در همه زمان ها - پروشات']
['10 پرنسس محبوب دخترها در دنیای انیمیشن های دیزنی - پروشات']
['معرفی بهترین فیلم های ژانر فانتزی تاریخ سین

['آخر هفته با طعم فیلم! (شماره 114)']
['پروشات - صفحه 2 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 4 از 348 - مجله آنلاین سینما و سرگرمی']
['لیست بهترین فیلم\u200cهای فمینیستی تاریخ سینما که باید تماشا کنید']
['بهترین فیلم\u200cهای کمدی سال 2020 به ترتیب رتبه بندی که باید تماشا کنید']
['بهترین فیلم\u200cهای عجیب کمدی که شاید تا به حال تماشا نکرده باشید']
['پروشات - صفحه 8 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 5 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 6 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 3 از 348 - مجله آنلاین سینما و سرگرمی']
['بهترین فیلم های دنزل واشینگتن که باید ببینید - پروشات']
['لیست بهترین فیلم\u200cهای جانی دپ که باید تماشا کنید']
---user: 04dee882-21854-4c99a-a5651-1c97548211672 ---
what user saw:
['معرفی 13 سریال جذاب و دیدنی شبیه "اسپارتاکوس" (Spartacus) - پروشات']
['معرفی 12 سریال جذاب و دیدنی شبیه "مردگان متحرک" (The Walking Dead) - پروشات']
['معرفی 15 سریال جذاب و دیدنی شبیه "تین ولف" (Teen Wolf) - پروشات']
[]
['

['معرفی 13 سریال جذاب و دیدنی شبیه "گمشدگان" (Lost) - پروشات']
['لیست 30 فیلم برتر آخرالزمانی در تاریخ سینما که باید ببینید - پروشات']
['12 فیلم برتر تاریخ سینما با موضوع سونامی (Tsunami) - پروشات']
['لیست 50 تایی بهترین سریال های خارجی تاریخ سینما - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه "مکس دیوانه" (Mad Max) نسخه 1979 - پروشات']
['لیست 20 تایی از بهترین فیلم های ژانر کودک در سال 2019-2020 - پروشات']
['لیست بهترین فیلم های ترسناک درباره زامبی ها - پروشات']
['بهترین فیلم های فانتزی که در سال 2019-2020 اکران خواهند شد - پروشات']
---user: 27769071-146aa-a97fb-bec87-73b2389e97849 ---
what user saw:
['معرفی 18 فیلم جذاب و دیدنی این دهه درباره افراد دگرباش (LGBT) - پروشات']
['15 فیلم برتر اسکارلت جوهانسون که باید تماشا کنید - پروشات']
['معرفی فیلم های جذاب و دیدنی مشابه "زندگی ادل" (Blue is the Warmest Color) - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه "مالنا" (Malèna) - پروشات']
what we recommend:
['معرفی 18 فیلم جذاب و دیدنی این دهه درباره افراد دگرباش (LGBT) - پروشات']
['معرفی فیلم

In [25]:
for i in range(0,len(users_recoms2), 14):
    check(i)

---user: 02fb517a-85ee-4e5e-ce00-50c8f3c384d2 ---
what user saw:
['معرفی 25 فیلم با پیچیده ترین پایان بندی ها در تاریخ سینما - پروشات']
['12 فیلم برتر تاریخ سینما با محوریت CIA (سازمان سیا) - پروشات']
['لیست بهترین فیلم هایی که با موضوع فرار از زندان ساخته شده اند - پروشات']
['معرفی 10 فیلم جذاب و دیدنی درباره تروریسم که شاید دوست داشته باشید تماشا کنید - پروشات']
what we recommend:
['لیست زننده\u200cترین و زجرآورترین فیلم\u200cهای تاریخ سینما که هرگز فراموش نخواهید کرد - پروشات']
['لیست 20 تایی خشن ترین فیلم های تاریخ سینما که نباید از دست بدهید - پروشات']
['11 انیمه برتر تاریخ با موضوع فرشتگان که باید ببینید - پروشات']
['12 فیلم جذاب و دیدنی شبیه فیلم "تک تیرانداز آمریکایی" (American Sniper) که باید تماشا کنید - پروشات']
['20 فیلم برتر ژانر آدم ربایی در تاریخ سینما که باید ببینید - پروشات']
['بهترین فیلم های دنزل واشینگتن که باید ببینید - پروشات']
['معرفی بهترین فیلم های تاریخ سینما با موضوع اعتیاد و مواد مخدر - پروشات']
['معرفی 26 فیلم جذاب و دیدنی درباره سرقت در تاریخ سینما که باید

['10 فیلم جذاب و دیدنی شبیه فیلم "هفت" (Se7en) - پروشات']
['معرفی 25 کمدی محبوب و دیدنی مناسب بزرگسالان (R-Rated) - پروشات']
['معرفی 25 فیلم با پیچیده ترین پایان بندی ها در تاریخ سینما - پروشات']
['برترین فیلم\u200cهای قرن بیستم در مورد جادو و تردستی - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه سه گانه "ارباب حلقه ها" (The Lord of the Rings) - پروشات']
['معرفی 25 فیلم جذاب و دیدنی شبیه "جزیره شاتر" (Shutter Island) - پروشات']
['معرفی 17 فیلم جذاب و دیدنی درباره نوجوانان در این دهه (2019 تا 2010) - پروشات']
['بهترین فیلم های علمی تخیلی در قرن 21 (تا به اینجا) - پروشات']
['معرفی 10 فیلم جذاب و دیدنی شبیه "رستگاری در شاوشنک" (The Shawshank Redemption) - پروشات']
['بهترین فیلم های سال 2019 که با درجه سنی بزرگسال (R-Rated) اکران شدند - پروشات']
['معرفی 17 فیلم ترسناک و عذاب آور که نمی توانید بیش از یک بار تماشا کنید - پروشات']
---user: da11096e-5dc4-4058-c013-25bc71bc56a1 ---
what user saw:
['لیست 40 تایی بهترین فیلم های ایرانی در تاریخ سینمای ایران - پروشات']
['معرفی 18 فیلم غم انگیز تاریخ

['لیست بهترین فیلم های کمدی و حال خوب کن قرن 21 که خنده را به لبانتان می آورند - پروشات']
['بهترین فیلم های تاریخ سینما درباره خودکشی و مرگ - پروشات']
['معرفی 18 فیلم غم انگیز تاریخ سینما - پروشات']
['لیست 20 تایی خشن ترین فیلم های تاریخ سینما که نباید از دست بدهید - پروشات']
['20 فیلم تاثیرگذار درباره زنان با اراده و شجاع - پروشات']
['بهترین فیلم های علمی تخیلی در قرن 21 (تا به اینجا) - پروشات']
['20 فیلم پیچیده و تاثیرگذار برتر در تاریخ سینما - پروشات']
['12 فیلم برتر تاریخ سینما با موضوع سونامی (Tsunami) - پروشات']
['معرفی 7 فیلم جذاب و دیدنی شبیه "میان ستاره ای" (Interstellar) - پروشات']
['لیست برترین فیلم های اکشن تاریخ سینما با محوریت شخصیت زن - پروشات']
['بهترین فیلم های لئوناردو دیکاپریو که حتما باید تماشا کنید، 20 اثر ممتاز - پروشات']
---user: 1ab765b0-001cc-cdf4a-ae3dd-dded95baff1ea ---
what user saw:
['لیست انیمه ۹ تا از بهترین انیمه\u200cهای چینی به انتخاب پروشات - پروشات']
['اگر انیمه "بلیچ" (Bleach) را دوست دارید این 12 انیمه را تماشا کنید - پروشات']
['بهترین انیمه های سه

['معرفی 5 انیمه درباره نبرد و پیروزی که باید آنها تماشا کنید']
what we recommend:
['بهترین انیمه های مشابه “پنج قلوهای باکلاس” (The Quintessential Quintuplets)']
['7 انیمه جذاب و دیدنی شبیه انیمه "شوالیه و جادو" (Knight’s & Magic) که باید تماشا کنید - پروشات']
['معرفی 10 انیمه جذاب و دیدنی با ژانر حارم در سال 2019 که باید تماشا کنید - پروشات']
['معرفی بهترین انیمه های مشابه “موشوکو تنسی:تجسم بیکاری”']
['7 انیمه جذاب و دیدنی شبیه “هوریمیا” (Horimiya) که باید تماشا کنید']
['بهترین انیمه های شبیه “شیطان کش” (Demon Slayer: Kimetsu no Yaiba)']
['7 انیمه جذاب و دیدنی شبیه انیمه "بی نظم در دبیرستان جادو" (The Irregular at Magic High School) - پروشات']
['۵ انیمه شبیه "Tensei shitara Slime Datta Ken" که باید تماشا کنید - پروشات']
['15 انیمه جذاب و دیدنی شبیه انیمه “به اوج رسیدن خوره کتاب” (Ascendance Of A Bookworm)']
['معرفی 5 انیمه درباره نبرد و پیروزی که باید آنها تماشا کنید']
['12 انیمه جذاب و دیدنی با موضوع خون آشامی - پروشات']
['7 انیمه جذاب و دیدنی شبیه انیمه "بنانا فیش" (Banana Fish) که 

['لیست بهترین فیلم\u200cهای فمینیستی تاریخ سینما که باید تماشا کنید']
['معرفی فیلم “قول\u200cهای شرقی” (Eastern Promises)']
['معرفی بهترین سیکوئل فیلم\u200cهای ابرقهرمانی که باید آنها را تماشا کنید']
['معرفی فیلم “پانصد روز سامر” (500Days of Summer)']
['لیست بهترین فیلم\u200cها درباره مشکلات خانوادگی که باید تماشا کنید']
['معرفی بهترین فیلم\u200cهای مشابه “بااستعداد” (Gifted) که باید تماشا کنید']
['“آواتار” مجددا به پرفروش\u200cترین فیلم تاریخ سینما تبدیل شد']
['معرفی فیلم “فارگو” (Fargo)']
what we recommend:
['آخر هفته با طعم فیلم! (شماره 114)']
['معرفی بهترین فیلم\u200cهای مشابه “بااستعداد” (Gifted) که باید تماشا کنید']
['لیست بهترین فیلم\u200cها درباره مشکلات خانوادگی که باید تماشا کنید']
['لیست بهترین فیلم\u200cهای جانی دپ که باید تماشا کنید']
['لیست بهترین فیلم\u200cهای فمینیستی تاریخ سینما که باید تماشا کنید']
['معرفی بهترین سیکوئل فیلم\u200cهای ابرقهرمانی که باید آنها را تماشا کنید']
['10 فیلم برتر جولیان مور که باید تماشا کنید - پروشات']
['معرفی فیلم “پانصد روز سامر” (500Days o

...

['10 فیلم برتر درباره جنگ جهانی دوم در تاریخ سینما - پروشات']
['معرفی 17 فیلم جذاب و دیدنی درباره نوجوانان در این دهه (2019 تا 2010) - پروشات']
['معرفی 10 فیلم دیوانه کننده که با الهام از داستان های واقعی ساخته شده اند - پروشات']
['12 فیلم برتر درباره نازی ها در تاریخ سینما - پروشات']
['معرفی 12 سریال جذاب و دیدنی با مدت زمان 20 تا 30 دقیقه - پروشات']
['معرفی 25 فیلم با پیچیده ترین پایان بندی ها در تاریخ سینما - پروشات']
['12 انیمه برتر تاریخ درباره غذا و آشپزی - پروشات']
['انیمه لیست 50 تایی از بهترین انیمه های سریالی تاریخ به انتخاب پروشات - پروشات']
['10 فیلم برتر تاریخ سینما با محوریت جنگ ویتنام - پروشات']
['نگاهی به ۱۰ شاهکار برتر سینمای روسیه (بهترین فیلم های سینمای روسیه) - پروشات']
---user: 6700c08f-7cd5-4881-c891-80567ccf9f4e ---
what user saw:
[]
[]
[]
what we recommend:
['پروشات: مطالب جذاب و خواندنی درباره سبک زندگی، سینما، فرهنگ و هنر، کسب و کار، گردشگری، مد و لباس، سلامت و ده\u200cها موضوع کاربردی دیگر']
['بهترین انیمه های مشابه “پنج قلوهای باکلاس” (The Quintessential Qui

['12 فیلم برتر درباره نازی ها در تاریخ سینما - پروشات']
['بهترین فیلم های تاریخ سینما با موضوع هولوکاست - پروشات']
['20 فیلم برتر تاریخ درباره بردگی - پروشات']
['معرفی بهترین فیلم\u200cهای مشابه “بااستعداد” (Gifted) که باید تماشا کنید']
['بهترین بازیگران زن تاریخ سینمای جهان چه کسانی هستند؟ - پروشات']
['بیوگرافی تیلدا سوئینتن از کودکی تا امروز + تصاویر - پروشات']
['معرفی فیلم “فارگو” (Fargo)']
['۱۰ کارگردان نابغه ای که به دنیا آمدند تا این ۱۰ فیلم را بسازند! - پروشات']
['بیوگرافی کامل کیت وینسلت بازیگر تایتانیک + تصاویر - پروشات']
---user: d94a1cda-aa47d-d6be2-2df5e-eddea41fcb990 ---
what user saw:
['معرفی بهترین فیلم های ژانر فانتزی تاریخ سینما که باید تماشا کنید - پروشات']
['معرفی 18 فیلم غم انگیز تاریخ سینما - پروشات']
['بهترین فیلم های عاشقانه غم انگیز در تاریخ سینما - پروشات']
what we recommend:
['معرفی 18 فیلم غم انگیز تاریخ سینما - پروشات']
['معرفی بهترین فیلم های ژانر فانتزی تاریخ سینما که باید تماشا کنید - پروشات']
['بهترین فیلم های عاشقانه غم انگیز در تاریخ سینما - پروشات']
[

what user saw:
['7 فیلم رزمی جذاب و دیدنی شبیه فیلم "بچه کاراته\u200cکار" (The Karate Kid) که باید تماشا کنید - پروشات']
['معرفی بهترین سیکوئل فیلم\u200cهای ابرقهرمانی که باید آنها را تماشا کنید']
['معرفی بهترین فیلم\u200cهای مشابه “بااستعداد” (Gifted) که باید تماشا کنید']
what we recommend:
['معرفی بهترین سیکوئل فیلم\u200cهای ابرقهرمانی که باید آنها را تماشا کنید']
['معرفی بهترین فیلم\u200cهای مشابه “بااستعداد” (Gifted) که باید تماشا کنید']
['7 فیلم رزمی جذاب و دیدنی شبیه فیلم "بچه کاراته\u200cکار" (The Karate Kid) که باید تماشا کنید - پروشات']
['لیست بهترین فیلم\u200cها درباره مشکلات خانوادگی که باید تماشا کنید']
['آخر هفته با طعم فیلم! (شماره 114)']
['10 فیلم برتر جولیان مور که باید تماشا کنید - پروشات']
['معرفی انیمه Psycho-pass ؛ هیجان مبارزه در دنیای آینده']
['10 فیلم جذاب و دیدنی درباره نوجوانان در سال 2019 که باید تماشا کنید - پروشات']
['بهترین انیمه های اکشن که تاکنون ساخته شده اند - پروشات']
['لیست 20 تایی از بهترین فیلم های ژانر کودک در سال 2019-2020 - پروشات']
['بهترین فیلم

['20 کتابی که زندگی شما را متحول می کنند و بهتر است که قبل از 30 سالگی خوانده شوند - پروشات']
---user: 4e200f1e-ec5a-4815-c809-bebdb0da9c36 ---
what user saw:
['لیست 24 تایی طولانی ترین انیمه های سریالی که تاکنون ساخته شده اند - پروشات']
['لیست زننده\u200cترین و زجرآورترین فیلم\u200cهای تاریخ سینما که هرگز فراموش نخواهید کرد - پروشات']
['معرفی تمام ژانرهای انیمه و مانگا به همراه انیمه لیست و توضیحات کامل - پروشات']
['معرفی 10 انیمه جذاب و دیدنی با ژانر حارم در سال 2019 که باید تماشا کنید - پروشات']
['معرفی بهترین انیمه های مشابه “موشوکو تنسی:تجسم بیکاری”']
what we recommend:
['معرفی تمام ژانرهای انیمه و مانگا به همراه انیمه لیست و توضیحات کامل - پروشات']
['معرفی 10 انیمه جذاب و دیدنی با ژانر حارم در سال 2019 که باید تماشا کنید - پروشات']
['لیست 24 تایی طولانی ترین انیمه های سریالی که تاکنون ساخته شده اند - پروشات']
['لیست زننده\u200cترین و زجرآورترین فیلم\u200cهای تاریخ سینما که هرگز فراموش نخواهید کرد - پروشات']
['معرفی بهترین انیمه های مشابه “موشوکو تنسی:تجسم بیکاری”']
['بهترین انیمه

['50 فیلم ابرقهرمانی برتر تاریخ سینما تا به امروز + تصاویر - صفحه 4 از 5 - پروشات']
['50 فیلم ابرقهرمانی برتر تاریخ سینما تا به امروز + تصاویر - صفحه 2 از 5 - پروشات']
['50 فیلم ابرقهرمانی برتر تاریخ سینما تا به امروز + تصاویر - صفحه 3 از 5 - پروشات']
['50 فیلم ابرقهرمانی برتر تاریخ سینما تا به امروز + تصاویر - صفحه 5 از 5 - پروشات']
['50 فیلم ابرقهرمانی برتر تاریخ سینما تا به امروز + تصاویر - پروشات']
['10 حقیقت درباره "سوپرمن" که فقط طرفداران کمیک از آن خبر دارند - پروشات']
['رتبه\u200cبندی تمام 23 فیلم\u200c دنیای سینمایی مارول (MCU)، از بدترین تا بهترین - پروشات']
['معرفی بهترین سیکوئل فیلم\u200cهای ابرقهرمانی که باید آنها را تماشا کنید']
['معرفی بدترین فیلم\u200cهای سال 2020 تا به اینجا - پروشات']
['معرفی تمام ژانرهای انیمه و مانگا به همراه انیمه لیست و توضیحات کامل - پروشات']
['8 فیلم برتر تاریخ درباره خدایان و اساطیر یونان به همراه تریلر - پروشات']
['برترین فیلم\u200cهای قرن بیستم در مورد جادو و تردستی - پروشات']
---user: b67dfd4e-e8665-5f052-279f9-9d7318198ce88 ---
what user sa